In [18]:
import pandas as pd
import spacy
import random
from spacy import displacy
from spacy.training.example import Example
import os
import re
import string
import nltk
import json

from nltk.stem.porter import PorterStemmer
#!pip install spacy
#!python -m spacy download en_core_web_sm
print("SpacyVersion - ",spacy.__version__)

SpacyVersion -  3.2.0


### generate train data

Train data needs to have merchant raw name and start and end indices 

In [20]:
def cleanUpSpecialChar(rawname):
    rawname = re.sub(r"[^a-zA-Z0-9]"," ",rawname)
    rawname = " ".join(rawname.split())
   
    return rawname


def generateIndices():
    df_train = '../data/df_train_raw.csv'
    df_train_spacy = '../data/df_train_spacy1.csv'
    no_duplicates = set()
    with open(df_train,'r') as inputfile:
        with open(df_train_spacy, "w") as outputfile:    
            next(inputfile)
            for line in inputfile:
                lineArr = line.split(',')
                rawname = lineArr[3].strip()
                cleanedname = lineArr[6].strip()               
                rawname = cleanUpSpecialChar(rawname)
                #print(rawname, cleanedname)
                          
                #get the cleaned name cleand to find the index in raw name                
                
                mname = cleanedname.strip()
                
                mnames = mname.split(' ')
                startIdx=0
                endIdx=len(mnames[0].strip())
                
                if len(mnames)>1 and len(mnames[0].strip()) < 2:
                    endIdx = endIdx+1+len(mnames[1].strip())   
                    
                if len(mnames)>2 and len(mnames[0].strip()) < 2 and len(mnames[1].strip()) < 2:
                    endIdx = endIdx+1+len(mnames[2].strip())   
                             
                        
                newcleanedname = mname[startIdx:endIdx]
                #print('new cleaned name:', cleanedname)
                
                newstartidx = rawname.strip().lower().find(newcleanedname)
                
                if newstartidx == -1:
                    continue
                    
                newEndIdx = newstartidx + len(newcleanedname.strip())               
                #print('newstartidx:', newstartidx,'newEndIdx:',newEndIdx)             
                
                
                newline = rawname.strip()+','+str(newstartidx)+','+str(newEndIdx)+','+ rawname[newstartidx:newEndIdx]   
                
                if newline not in no_duplicates:
                    outputfile.write(newline+'\n')
                    no_duplicates.add(newline)
                #break
 


def generateTrainData():
    df_train_spacy = '../data/df_train_spacy1.csv'
    train_spacy_data = []
    with open(df_train_spacy,'r') as inputfile:
        for line in inputfile:
            lineArr = line.split(',')
            train_spacy_data.append((lineArr[0].strip(),{'entities':[(int(lineArr[1]),int(lineArr[2]),'MN')]}))
            #break
    return train_spacy_data      

               
generateIndices()
train_data_main = generateTrainData()
train_data_main[0:100]



[('SQ PG POOL Mount Rainier MD', {'entities': [(0, 2, 'MN')]}),
 ('APPLE COM BILL 866 712 7753 CA', {'entities': [(0, 5, 'MN')]}),
 ('SIE PLAYSTATIONNETWORK 877 971 7669 CA', {'entities': [(0, 3, 'MN')]}),
 ('APPLE COM BILL www apple com CA', {'entities': [(0, 5, 'MN')]}),
 ('Amazon com Amzn com bill WA', {'entities': [(0, 6, 'MN')]}),
 ('AMAZON COM AMZN COM BILL WA', {'entities': [(0, 6, 'MN')]}),
 ('PLAYSTATION NETWORK 800 345 7669 CA', {'entities': [(0, 11, 'MN')]}),
 ('REG LOUISIANA 14 0664 BOSSIER CITY LA', {'entities': [(0, 3, 'MN')]}),
 ('MCDONALD S F3955 INDIANAPOLIS IN', {'entities': [(0, 8, 'MN')]}),
 ('NINTENDO AMERICAUS 800 255 3700 WA', {'entities': [(0, 8, 'MN')]}),
 ('DUNKIN 330016 Q35 STROUDSBURG PA', {'entities': [(0, 6, 'MN')]}),
 ('DUNKIN 306582 Q35 BRIGHTON MA', {'entities': [(0, 6, 'MN')]}),
 ('MICROSOFT ULTIMATE 1 M MSBILL INFO WA', {'entities': [(0, 9, 'MN')]}),
 ('BVD BEENVERIFIED COM 855 9046471 NY', {'entities': [(0, 3, 'MN')]}),
 ('XSOLLA ROBLOX H XSOLLA COM 

In [21]:
nlp = spacy.load('en_core_web_sm')

In [22]:
def train_spacy(data,iterations):
    TRAIN_DATA = data
    nlp = spacy.blank('en')  # create blank Language class
    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if 'ner' not in nlp.pipe_names:
        ner = nlp.add_pipe('ner')
        #nlp.add_pipe('ner', last=True)
    
    # add labels
    for _, annotations in TRAIN_DATA:
         for ent in annotations.get('entities'):
            ner.add_label(ent[2])
            
    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    with nlp.disable_pipes(*other_pipes):  # only train NER
        optimizer = nlp.begin_training()
        for itn in range(iterations):
            #print("Statring iteration " + str(itn))
            random.shuffle(TRAIN_DATA)
            losses = {}
            for text, annotations in TRAIN_DATA:
                doc = nlp.make_doc(text)
                example = Example.from_dict(doc, annotations)
                # Update the model
                nlp.update([example], losses=losses, drop=0.3)                
            print(losses)
    return nlp


################# commented this part as model takes time to run - un comment to train the model ############
#prdnlp = train_spacy(train_data_main, 20)

# Save our trained Model
#modelfile = 'spacymodelMainRaw'#input("Enter your Model Name: ")
#prdnlp.to_disk(modelfile)


{'ner': 1077.2639633061765}
{'ner': 387.46433811936237}
{'ner': 279.94820134359605}
{'ner': 251.16090548254115}
{'ner': 193.98285287368603}
{'ner': 186.44054817108395}
{'ner': 151.78907749481255}
{'ner': 136.43217221514467}
{'ner': 147.9046095030848}
{'ner': 144.61287895665362}
{'ner': 172.89279397354244}
{'ner': 172.07093837185135}
{'ner': 137.29599983685299}
{'ner': 121.5854464478735}
{'ner': 130.46508957645128}
{'ner': 158.49538574452606}
{'ner': 133.2839437912357}
{'ner': 134.9135257851325}
{'ner': 113.50249649217602}
{'ner': 163.62408536177088}


### Testing the model

In [23]:
nlp1 = spacy.load("spacymodelMainRaw")
test_text = cleanUpSpecialChar("APPLE.com asdfsdklfjd ")
doc = nlp1(test_text)
for ent in doc.ents:
    print(test_text ,'= ', ent.text, ent.start_char, ent.end_char, ent.label_)
    
    


APPLE com asdfsdklfjd =  APPLE 0 5 MN


In [24]:
nlp1 = spacy.load("spacymodelMainRaw")

#lost test data
df_test = pd.read_csv("../data/df_test.csv")
output_test = '../data/test_output.csv'

with open(output_test, 'w', newline='') as outputfile:    
    for index, row in df_test.iterrows(): 
        #Test your text
        test_text = cleanUpSpecialChar(row[0])
        doc = nlp1(test_text)
        for ent in doc.ents:
            #print(test_text ,'= ', ent.text, ent.start_char, ent.end_char, ent.label_)
            arr= [test_text,ent.text, str(ent.start_char), str(ent.end_char),ent.label_]
            outputfile.write(",".join(arr)+'\n')
        

     
        
        

### running back on train model for report

In [25]:
#test train data again
df_train_raw = pd.read_csv("../data/df_train_raw.csv")
output_train = '../data/train_output.csv'

with open(output_train, 'w', newline='') as outputfile:    
    outputfile.write("auth_ts,mcc,mid,auth_merch_name,auth_amt,local_amt,state,city,mname,test_text,refined_mer_name, start_char, end_char,label_ \n") # header
    for index, row in df_train_raw.iterrows():         
        #Test your text
        test_text = cleanUpSpecialChar(row[3])
        doc = nlp1(test_text)
        for ent in doc.ents:
            arr= [str(row[0]),str(row[1]),str(row[2]),str(row[3]),str(row[4]),str(row[5]),str(row[6]),str(row[7]),str(row[8]),str(test_text),str(ent.text), str(ent.start_char), str(ent.end_char),str(ent.label_)]
            print(arr)
            outputfile.write(",".join(arr)+'\n')

['2021-08-29 08:20:50.000', '7999', '188418000053360', 'SQ *PG POOL            Mount Rainier MD ', '1.0', '1.0', 'sq pg pool mount rainier md', 'sq pg pool mount rainier', 'md', 'SQ PG POOL Mount Rainier MD', 'SQ', '0', '2', 'MN']
['2021-08-14 01:41:27.000', '5815', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '12.83', '12.83', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-14 01:45:28.000', '5818', '342475000144509', 'SIE*PLAYSTATIONNETWORK 877-971-7669  CA ', '4.97', '4.97', 'sie playstationnetwork ca', 'sie playstationnetwork', 'ca', 'SIE PLAYSTATIONNETWORK 877 971 7669 CA', 'SIE', '0', '3', 'MN']
['2021-08-03 06:14:58.000', '5815', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '0.0', '0.0', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 08:14:41.000', '5735', '311204598883   ', 'APPLE.COM/BILL         www.apple.com CA ', '9.99', '9.99', 'apple appl

['2021-08-29 17:51:55.000', '5814', '501684000000000', 'SONIC DRIVE IN #4817   WILMER        TX ', '2.48', '2.48', 'sonic drive in wilmer tx', 'sonic drive in wilmer', 'tx', 'SONIC DRIVE IN 4817 WILMER TX', 'SONIC', '0', '5', 'MN']
['2021-08-10 04:14:44.000', '5817', '527021000211443', 'GOOGLE* ROBLOX         Mountain View CA ', '1.07', '1.07', 'google roblox mountain view ca', 'google roblox ', 'ca', 'GOOGLE ROBLOX Mountain View CA', 'GOOGLE', '0', '6', 'MN']
['2021-08-03 06:04:54.000', '5815', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '0.0', '0.0', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-15 02:41:23.000', '5735', '311204403886   ', 'APPLE.COM/BILL         www.apple.com CA ', '15.99', '15.99', 'apple apple com ca', 'apple apple com', 'ca', 'APPLE COM BILL www apple com CA', 'APPLE', '0', '5', 'MN']
['2021-08-03 05:32:43.000', '5815', '337186000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '15.91', '15.

['2021-08-29 17:52:35.000', '5735', '311204403886   ', 'APPLE.COM/BILL         www.apple.com CA ', '4.99', '4.99', 'apple apple com ca', 'apple apple com', 'ca', 'APPLE COM BILL www apple com CA', 'APPLE', '0', '5', 'MN']
['2021-08-03 06:07:54.000', '3690', '030000103455001', 'COURTYARD BY MARRIOT   SAN MARCOS    TX ', '8.98', '8.98', 'courtyard by marriot san marcos tx', 'courtyard by marriot ', 'tx', 'COURTYARD BY MARRIOT SAN MARCOS TX', 'COURTYARD', '0', '9', 'MN']
['2021-08-10 09:24:25.000', '5814', '000000010737370', 'VENDING NEW START VENT ROSEDALE      NY ', '3.5', '3.5', 'vending new start vent rosedale ni', 'vending new start vent rosedale', 'ni', 'VENDING NEW START VENT ROSEDALE NY', 'VENDING', '0', '7', 'MN']
['2021-08-10 04:07:58.000', '5735', '311204403886   ', 'APPLE.COM/BILL         www.apple.com CA ', '59.07', '59.07', 'apple apple com ca', 'apple apple com', 'ca', 'APPLE COM BILL www apple com CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 17:43:52.000', '4899', '527021000

['2021-08-15 02:39:14.000', '5815', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '0.99', '0.99', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 07:58:34.000', '5999', '520004287347   ', 'TELETIES               MAITLAND      FL ', '13.59', '13.59', 'teleties maitland fl', 'teleties maitland', 'fl', 'TELETIES MAITLAND FL', 'TELETIES', '0', '8', 'MN']
['2021-08-29 17:49:26.000', '5968', '089047000762203', 'Amazon Prime           Amzn.com/bill WA ', '128.82', '128.82', 'amazon prime amzn wa', 'amazon prime amzn', 'wa', 'Amazon Prime Amzn com bill WA', 'Amazon', '0', '6', 'MN']
['2021-09-09 06:59:32.000', '5812', '1VKWOGBF44BU45L', 'DOORDASH*CHICK-FIL-A   +16506819470  CA ', '14.64', '14.64', 'doordash chick fil ca', 'doordash chick fil', 'ca', 'DOORDASH CHICK FIL A 16506819470 CA', 'DOORDASH', '0', '8', 'MN']
['2021-09-09 08:50:05.000', '5735', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '47.69', '47.6

['2021-09-09 06:39:49.000', '5812', '4445040872889  ', 'TST* NOTHING BUNDT CAK SOUTHLAKE     TX ', '53.0', '53.0', 'tst nothing bundt cak southlake tx', 'tst nothing bundt cak southlake', 'tx', 'TST NOTHING BUNDT CAK SOUTHLAKE TX', 'TST', '0', '3', 'MN']
['2021-08-10 03:59:32.000', '4899', '248750000103177', 'GOOGLE *Mazzocchi      650-253-0000  CA ', '2.16', '2.16', 'google mazzocchi ca', 'google mazzocchi', 'ca', 'GOOGLE Mazzocchi 650 253 0000 CA', 'GOOGLE', '0', '6', 'MN']
['2021-08-29 17:48:18.000', '5968', '089047000762203', 'Amazon Prime           Amzn.com/bill WA ', '13.77', '13.77', 'amazon prime amzn wa', 'amazon prime amzn', 'wa', 'Amazon Prime Amzn com bill WA', 'Amazon', '0', '6', 'MN']
['2021-08-03 06:22:39.000', '5735', '311204403886   ', 'APPLE.COM/BILL         CUPERTINO     CA ', '0.0', '0.0', 'apple cupertino ca', 'apple cupertino', 'ca', 'APPLE COM BILL CUPERTINO CA', 'APPLE', '0', '5', 'MN']
['2021-08-10 15:33:15.000', '5814', '446187000000000', 'DD/BR #344467       

...

['2021-08-29 10:03:41.000', '5816', '145376000144509', 'PLAYSTATION NETWORK    800-345-7669  CA ', '0.0', '0.0', 'playstation network ca', 'playstation network', 'ca', 'PLAYSTATION NETWORK 800 345 7669 CA', 'PLAYSTATION', '0', '11', 'MN']
['2021-08-10 09:18:21.000', '5812', '4445024989962  ', 'CKE*THE BREAD HOUSE  5 ALBANY        GA ', '12.53', '12.53', 'cke bread house albany ga', 'cke bread house ', 'ga', 'CKE THE BREAD HOUSE 5 ALBANY GA', 'CKE', '0', '3', 'MN']
['2021-08-10 06:54:31.000', '5814', '967000000000001', 'USA SODA SNA*USA*FIVE  SMYRNA        GA ', '1.5', '1.5', 'usa soda sna usa five smyrna ga', 'usa soda sna usa five ', 'ga', 'USA SODA SNA USA FIVE SMYRNA GA', 'USA', '0', '3', 'MN']
['2021-08-29 08:21:28.000', '4899', '248750000103177', 'GOOGLE *ROBLOX         650-253-0000  CA ', '1.05', '1.05', 'google roblox ca', 'google roblox', 'ca', 'GOOGLE ROBLOX 650 253 0000 CA', 'GOOGLE', '0', '6', 'MN']
['2021-08-29 06:51:12.000', '4816', '000174030076999', 'PAYPAL              

['2021-08-03 05:54:17.000', '4816', '000311161458881', 'MICROSOFT*XBOX         MSBILL.INFO   WA ', '8.65', '8.65', 'microsoft xbox msbill info wa', 'microsoft xbox msbill info', 'wa', 'MICROSOFT XBOX MSBILL INFO WA', 'MICROSOFT', '0', '9', 'MN']
['2021-08-10 09:11:59.000', '5812', '000021675634000', 'SMOOTHIE FACTORY #4110 DALLAS        TX ', '5.51', '5.51', 'smoothie factory dallas tx', 'smoothie factory ', 'tx', 'SMOOTHIE FACTORY 4110 DALLAS TX', 'SMOOTHIE', '0', '8', 'MN']
['2021-08-15 02:19:22.000', '5735', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '10.99', '10.99', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 17:39:29.000', '4899', '248750000103177', 'GOOGLE *ROBLOX         650-253-0000  CA ', '0.99', '0.99', 'google roblox ca', 'google roblox', 'ca', 'GOOGLE ROBLOX 650 253 0000 CA', 'GOOGLE', '0', '6', 'MN']
['2021-08-10 14:39:34.000', '5816', '145376000144509', 'PLAYSTATION NETWORK    800-345-7669  CA ', 

['2021-08-29 17:35:48.000', '5818', '342475000144509', 'SIE*PLAYSTATIONNETWORK 877-971-7669  CA ', '9.99', '9.99', 'sie playstationnetwork ca', 'sie playstationnetwork', 'ca', 'SIE PLAYSTATIONNETWORK 877 971 7669 CA', 'SIE', '0', '3', 'MN']
['2021-08-15 02:35:13.000', '5815', '337190000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '2.99', '2.99', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 17:45:28.000', '5818', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '0.0', '0.0', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 07:08:36.000', '5942', '235251000762203', 'AMZN Mktp US           Amzn.com/bill WA ', '14.34', '14.34', 'amzn mktp us amzn wa', 'amzn mktp us amzn', 'wa', 'AMZN Mktp US Amzn com bill WA', 'AMZN', '0', '4', 'MN']
['2021-08-29 17:43:07.000', '5816', '145376000144509', 'PLAYSTATION NETWORK    800-345-7669  CA ', '108.24', '108.24', 'playstation ne

['2021-08-29 08:27:14.000', '5411', 'YJAFPWST3ICXIAV', 'INSTACART              +18882467822  CA ', '0.0', '0.0', 'instacart ca', 'instacart', 'ca', 'INSTACART 18882467822 CA', 'INSTACART', '0', '9', 'MN']
['2021-08-29 17:35:27.000', '5818', '527021000205205', 'Microsoft*Xbox         msbill.info   WA ', '9.99', '9.99', 'microsoft xbox msbill info wa', 'microsoft xbox msbill info', 'wa', 'Microsoft Xbox msbill info WA', 'Microsoft', '0', '9', 'MN']
['2021-08-10 04:03:04.000', '5815', '112137000108778', 'APPLE.COM/BILL         866-712-7753  CA ', '10.69', '10.69', 'apple ca', 'apple', 'ca', 'APPLE COM BILL 866 712 7753 CA', 'APPLE', '0', '5', 'MN']
['2021-08-29 10:03:53.000', '5814', '319471000000000', 'DUNKIN #302560 Q35     CINCINNATI    OH ', '3.89', '3.89', 'dunkin cincinnati oh', 'dunkin ', 'oh', 'DUNKIN 302560 Q35 CINCINNATI OH', 'DUNKIN', '0', '6', 'MN']
['2021-08-29 17:09:52.000', '5945', '000174101920992', 'PAYPAL *EPIC GAMES     4029357733    NC ', '21.26', '21.26', 'paypal epic

UnicodeEncodeError: 'charmap' codec can't encode character '\ufffd' in position 62: character maps to <undefined>